# Run Delphes and extract observables

Johann Brehmer, Kyle Cranmer, Marco Farina, Felix Kling, Duccio Pappadopulo, Josh Ruderman 2018

In [1]:
from __future__ import absolute_import, division, print_function, unicode_literals

import numpy as np
import matplotlib
from matplotlib import pyplot as plt
%matplotlib inline
import logging
import os
import math
from collections import OrderedDict

from madminer.delphes import DelphesProcessor
from madminer.sampling import combine_and_shuffle
from madminer.utils.particle import MadMinerParticle


In [2]:
logging.basicConfig(
    format='%(asctime)-5.5s %(name)-20.20s %(levelname)-7.7s %(message)s',
    datefmt='%H:%M',
    level=logging.INFO
)

for key in logging.Logger.manager.loggerDict:
    if "madminer" not in key:
        logging.getLogger(key).setLevel(logging.WARNING)

In [3]:
base_dir = '/Users/johannbrehmer/work/projects/madminer/diboson_mining/'
mg_dir = '/Users/johannbrehmer/work/projects/madminer/MG5_aMC_v2_6_4/'

In [4]:
sample_dir = base_dir + 'data/samples/wgamma_sys/'
card_dir = base_dir + 'cards/wgamma/'
ufo_model_dir = card_dir + 'SMWgamma_UFO'
run_card_dir = card_dir + 'run_cards/'
mg_process_dir = base_dir + 'data/mg_processes/wgamma_sys/'
log_dir = base_dir + 'logs/wgamma_sys/'
temp_dir = base_dir + 'data/temp'
delphes_dir = mg_dir + 'Delphes'

## Observables and cuts

In [5]:
def calculate_mt(leptons, photons, jets, met):
    # Particles
    if len(leptons) < 1:
        raise RuntimeError()
    
    l = leptons[0]
    
    # Transverse mass and Delta
    cos_delta_phi = np.cos(l.phi() - met.phi())
    mt = (2 * l.pt * met.pt * (1. - cos_delta_phi))**0.5
    
    return mt

In [6]:
def calculate_phi(leptons, photons, jets, met, eta_solution=0):
    # Parameters
    mw = 80.4
    
    # Particles
    if len(leptons) < 1 or len(photons) < 1:
        raise RuntimeError()
    
    l = leptons[0]
    a = photons[0]
    
    # Transverse mass and Delta
    mt = calculate_mt(leptons, photons, jets, met)
    deltasq = 0.
    if met.pt > 0. and l.pt > 0.:
        deltasq = (mw**2 - mt**2) / (2. * met.pt * l.pt)
    
    # v reconstruction, "normal" case
    if deltasq > 0.:
        # Two solutions
        temp = np.log(1 + deltasq**0.5 * (2 + deltasq)**0.5 + deltasq)
        eta_v_plus = l.eta + temp
        eta_v_minus = l.eta - temp
        
        # Select one of them
        if eta_solution > 0:
            eta_v = eta_v_plus
        elif eta_solution < 0:
            eta_v = eta_v_minus
        else:
            dice = np.random.rand()
            if dice > 0.5:
                eta_v = eta_v_plus
            else:
                eta_v = eta_v_minus
            
    # v reconstruction, "other" case
    else:
        eta_v = l.eta
        
    # v particle
    v = MadMinerParticle()
    v.setptetaphim(met.pt, eta_v, met.phi(), 0.)
    
    # W and Wgamma reconstruction
    w = l + v
    vv = w + a
    
    # Boost into VV frame
    v_ = v.boost(vv.boostvector)
    l_ = l.boost(vv.boostvector)
    a_ = a.boost(vv.boostvector)
    w_ = w.boost(vv.boostvector)
    r_ = vv # vv.boost(vv.boostvector)

    # Calculate axes of "special frame" (1708.07823)
    z_ = w_.vector.unit()
    x_ = (r_.vector - z_ * r_.vector.dot(z_)).unit()
    y_ = z_.cross(x_)
    
    # Calculate x and y components of lepton wrt special x_, y_, z_ system
    lx_ = l_.vector.dot(x_)
    ly_ = l_.vector.dot(y_)
    
    # Calculate phi
    phi = math.atan2(ly_, lx_)
    
    return phi
    
    
def calculate_phi_minus(leptons, photons, jets, met):
    return calculate_phi(leptons, photons, jets, met, eta_solution=-1)
    
    
def calculate_phi_plus(leptons, photons, jets, met):
    return calculate_phi(leptons, photons, jets, met, eta_solution=1)

In [7]:
def setup_observables(delphesprocessor):
    delphesprocessor.reset_observables()
    
    # Default observables (four-momenta of a, l, j, and met)
    delphesprocessor.add_default_observables(
        n_leptons_max=1,
        n_photons_max=1,
        n_jets_max=1,
        include_charge=False,
        include_numbers=False,
        include_met=True
    )
    # Lepton flavour
    delphesprocessor.add_observable('pdgid_l1', 'l[0].pdgid', required=True)

    # Two-particle systems
    delphesprocessor.add_observable('m_la', '(l[0] + a[0]).m', required=True)
    delphesprocessor.add_observable('m_lmet', '(l[0] + met).m', required=True)
    delphesprocessor.add_observable('m_amet', '(a[0] + met).m', required=True)
    delphesprocessor.add_observable('pt_la','(l[0] + a[0]).pt', required=True)
    delphesprocessor.add_observable('pt_lmet','(l[0] + met).pt', required=True)
    delphesprocessor.add_observable('pt_amet','(a[0] + met).pt', required=True)
    delphesprocessor.add_observable('deltaphi_la', 'l[0].phi() - a[0].phi()', required=True)
    delphesprocessor.add_observable('deltaphi_lmet', 'l[0].phi() - met.phi()', required=True)
    delphesprocessor.add_observable('deltaphi_amet', 'a[0].phi() - met.phi()', required=True)
    delphesprocessor.add_observable('deltaeta_la', 'l[0].eta - a[0].eta', required=True)

    # Three-particle system
    delphesprocessor.add_observable('m_almet', '(a[0] + l[0] + met).m', required=True)
    delphesprocessor.add_observable('pt_almet', '(a[0] + l[0] + met).pt', required=True)

    # mT(W) and ressurrection phi
    delphesprocessor.add_observable_from_function('mt', calculate_mt, required=True)
    delphesprocessor.add_observable_from_function('phi_minus', calculate_phi_minus, required=True)
    delphesprocessor.add_observable_from_function('phi_plus', calculate_phi_plus, required=True)
    delphesprocessor.add_observable_from_function('phi', calculate_phi, required=True)


In [8]:
def setup_cuts(delphesprocessor, use_tight_cuts=False, use_antitight_cuts=False):
    delphesprocessor.reset_cuts()
    
    if use_tight_cuts:
        delphesprocessor.add_cut('pt_a1 >= 300.')
        delphesprocessor.add_cut('pt_l1 >= 80.')
        delphesprocessor.add_cut('et_miss >= 80.')
        delphesprocessor.add_cut('(deltaphi_la**2 + deltaeta_la**2)**0.5 >= 3.')
        delphesprocessor.add_cut('eta_l1**2 < 2.4**2')
    elif use_antitight_cuts:
        delphesprocessor.add_cut('pt_a1 >= 20.')
        delphesprocessor.add_cut('pt_l1 >= 20.')
        delphesprocessor.add_cut('et_miss >= 20.')
        delphesprocessor.add_cut(
            'int(pt_a1 < 300.) + int(pt_l1 < 80.) + int(et_miss < 80.)'
            + ' + int((deltaphi_la**2 + deltaeta_la**2)**0.5 < 3.) + int(eta_l1**2 > 2.4**2) > 0'
        )
    else:
        delphesprocessor.add_cut('pt_a1 >= 20.')
        delphesprocessor.add_cut('pt_l1 >= 20.')
        delphesprocessor.add_cut('et_miss >= 20.')

## Main loop

In [9]:
n_runs_per_benchmark = 22  # Number of run_cards
n_oversampling = 2

In [10]:
run = 0

for i_card in range(n_runs_per_benchmark):
    logging.info('Starting analysis of runs for card {}'.format(i_card))
            
    # Load setup
    dp = DelphesProcessor(sample_dir + 'setup.h5')
    
    # Load events
    run = i_card + 1
    run_str = str(run)
    if len(run_str) < 2:
        run_str = '0' + run_str
    event_folder = mg_process_dir + 'Events/run_{}'.format(run_str)
    
    dp.add_sample(
        event_folder + '/tag_1_pythia8_events.hepmc.gz',
        delphes_filename=event_folder + '/tag_1_pythia8_events_delphes.root',
        lhe_filename=event_folder + '/unweighted_events.lhe.gz',
        sampled_from_benchmark='sm',
        weights="lhe",
    )
        
    # Run Delphes
    dp.run_delphes(
        delphes_directory=delphes_dir,
        delphes_card=card_dir + 'delphes_card.dat',
        log_file=log_dir + '/delphes_{}.log'.format(run - 1),
        initial_command='source activate python2',
    )
    
    # Set up observables
    setup_observables(dp)
    
    # Tight analysis
    # setup_cuts(dp, use_tight_cuts=True)
    # dp.analyse_delphes_samples(delete_delphes_files=False)
    # dp.save(sample_dir + 'samples_tight_{}.h5'.format(i_card))
    
    # Anti-tight analysis
    setup_cuts(dp, use_tight_cuts=False, use_antitight_cuts=True)
    dp.analyse_delphes_samples(delete_delphes_files=False)
    dp.save(sample_dir + 'samples_antitight_{}.h5'.format(i_card))
    
    # Loose analysis
    # setup_cuts(dp)
    # dp.analyse_delphes_samples(delete_delphes_files=True)
    # dp.save(sample_dir + 'samples_{}.h5'.format(i_card))


10:50 root                 INFO    Starting analysis of runs for card 0
10:50 madminer.utils.inter INFO    HDF5 file does not contain is_reference field.
10:57 madminer.delphes     INFO    Analysing Delphes sample /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/mg_processes/wgamma_sys/Events/run_01/tag_1_pythia8_events_delphes.root
11:05 madminer.utils.inter INFO      50857 / 100000 events pass everything
11:05 madminer.utils.inter WARNING Found 43 negative weights in event: OrderedDict([('sm', -0.001436022), ('1', -0.0014609474), ('2', -0.0014027724), ('3', -0.0014609474), ('4', -0.0014027724), ('5', -0.001436022), ('6', -0.0014412587), ('7', -0.00079571784), ('8', -0.0029484356), ('9', -5.7752738e-05), ('10', -0.0012879235), ('11', -0.0010777996), ('12', -0.0037404293), ('13', -0.0018042468), ('14', -0.001432757), ('15', -0.0017937322), ('16', -0.0013812183), ('17', -0.0026181739), ('18', 0.00016074887), ('19', -0.0012113525), ('20', -0.0010354339), ('21', 0.000399810

11:05 madminer.utils.inter WARNING Found 42 negative weights in event: OrderedDict([('sm', -0.001436022), ('1', -0.0015435211), ('2', -0.001335076), ('3', -0.0015435211), ('4', -0.001335076), ('5', -0.001436022), ('6', -0.0016876662), ('7', -0.00052030474), ('8', -0.0041440862), ('9', 0.00079971907), ('10', -0.0012140674), ('11', -0.0008656438), ('12', -0.0026404885), ('13', -0.001794223), ('14', -0.001408557), ('15', -0.0021576035), ('16', -0.0012777), ('17', -0.0032356518), ('18', 0.0017323408), ('19', -0.0010200152), ('20', -0.00090434049), ('21', 0.0015288961), ('22', -0.0014888775), ('23', -0.0015564797), ('24', -0.0016810174), ('25', -0.00078873304), ('26', -0.00018928354), ('27', -0.0004819934), ('28', -0.0021302484), ('29', -0.0039072775), ('30', -0.0019302188), ('31', -0.0011720572), ('32', -0.0022458472), ('33', -0.0014803459), ('34', -0.0019175716), ('35', -0.00082512411), ('36', -0.0013384393), ('37', -0.0013384393), ('38', -0.0014396579), ('39', -0.0012994514), ('morphing_

11:28 madminer.utils.inter WARNING Found 45 negative weights in event: OrderedDict([('sm', -0.001187168), ('1', -0.0013737039), ('2', -0.0010288629), ('3', -0.0013737039), ('4', -0.0010288629), ('5', -0.001187168), ('6', -0.0010397568), ('7', -0.0014261684), ('8', -0.00049370994), ('9', -0.0018830381), ('10', -0.0010675826), ('11', -0.001213241), ('12', -0.00026311021), ('13', -0.0012752527), ('14', -0.0011576313), ('15', -0.00062620201), ('16', -0.0013897266), ('17', -0.00087599119), ('18', -0.0013624947), ('19', -0.0013223155), ('20', -0.0013506712), ('21', -0.0040732038), ('22', -0.0014077043), ('23', -0.0011342), ('24', -0.0013866554), ('25', -0.0013902203), ('26', -0.0011740485), ('27', -0.0012522905), ('28', -0.0014048821), ('29', -0.00057073595), ('30', -0.00076246295), ('31', -0.0013339281), ('32', -0.0012225859), ('33', -0.0014121883), ('34', -0.0013029942), ('35', -0.0011796975), ('36', -0.0010321601), ('37', -0.0010321601), ('38', -0.001191029), ('39', -0.00093130652), ('mor

11:28 madminer.utils.inter WARNING Found 45 negative weights in event: OrderedDict([('sm', -0.001187168), ('1', -0.0012215068), ('2', -0.001140295), ('3', -0.0012215068), ('4', -0.001140295), ('5', -0.001187168), ('6', -0.00095228676), ('7', -0.0016439718), ('8', -6.6616891e-05), ('9', -0.0023811988), ('10', -0.0011226823), ('11', -0.0013458492), ('12', -0.00017291809), ('13', -0.0012494812), ('14', -0.0012004752), ('15', -0.0004632064), ('16', -0.0014262163), ('17', -0.00077518414), ('18', -0.0012863866), ('19', -0.0014201757), ('20', -0.0014073614), ('21', -0.004751434), ('22', -0.0013700233), ('23', -0.0011090716), ('24', -0.0013473532), ('25', -0.0013635472), ('26', -0.001180501), ('27', -0.0011507769), ('28', -0.0012749696), ('29', -0.00062625288), ('30', -0.00090756967), ('31', -0.0013271796), ('32', -0.0012178135), ('33', -0.0014164522), ('34', -0.001276663), ('35', -0.0011750309), ('36', -0.0011420932), ('37', -0.0011420932), ('38', -0.0011885501), ('39', -0.0010904912), ('morp

11:45 madminer.utils.inter WARNING Found 2 negative weights in event: OrderedDict([('sm', 0.000819475), ('1', 0.0009102625), ('2', 0.00073953178), ('3', 0.0009102625), ('4', 0.00073953178), ('5', 0.000819475), ('6', 0.00086739948), ('7', 0.0004146282), ('8', 0.0016319808), ('9', -0.00012016078), ('10', 0.00068721388), ('11', 0.0004509511), ('12', 0.00062624563), ('13', 0.0010692499), ('14', 0.00071019517), ('15', 0.0011809048), ('16', 0.00084904396), ('17', 0.0010502985), ('18', -0.00075513814), ('19', 0.00062582797), ('20', 0.00081861769), ('21', 0.00035293129), ('22', 0.00094065491), ('23', 0.0010397677), ('24', 0.0011242136), ('25', 0.00084663914), ('26', 0.00083104887), ('27', 0.00096347239), ('28', 0.0011642994), ('29', 0.00098034659), ('30', 0.00069250788), ('31', 0.00087037535), ('32', 0.00092860517), ('33', 0.0008615833), ('34', 0.00094835477), ('35', 0.00066068114), ('36', 0.00074157708), ('37', 0.00074157708), ('38', 0.00082179956), ('39', 0.00065213304), ('morphing_basis_vec

...

16:07 madminer.utils.inter WARNING Found 2 negative weights in event: OrderedDict([('sm', 4.80477e-07), ('1', 5.4736168e-07), ('2', 4.2478132e-07), ('3', 5.4736168e-07), ('4', 4.2478132e-07), ('5', 4.80477e-07), ('6', 4.7186658e-07), ('7', 1.3025194e-07), ('8', 3.002351e-06), ('9', -1.1930744e-07), ('10', 3.4584516e-07), ('11', 2.9013833e-07), ('12', 1.5207961e-07), ('13', 6.4689001e-07), ('14', 4.0308046e-07), ('15', 6.3838895e-07), ('16', 5.4906423e-07), ('17', 6.071518e-07), ('18', 7.5077123e-07), ('19', 3.3158057e-07), ('20', 4.5300967e-07), ('21', 3.6653362e-07), ('22', 5.9624536e-07), ('23', 4.4296768e-07), ('24', 6.8976463e-07), ('25', 6.2405109e-07), ('26', 4.8854116e-07), ('27', 4.9624263e-07), ('28', 1.0818232e-06), ('29', 1.7262827e-07), ('30', -2.2150473e-07), ('31', 5.0872754e-07), ('32', 5.205891e-07), ('33', 4.8847553e-07), ('34', 6.3298599e-07), ('35', 5.2397635e-07), ('36', 4.2482805e-07), ('37', 4.2482805e-07), ('38', 4.8053283e-07), ('39', 3.9532073e-07), ('morphing_

16:07 madminer.utils.inter WARNING Found 2 negative weights in event: OrderedDict([('sm', 4.80477e-07), ('1', 5.450686e-07), ('2', 4.26429e-07), ('3', 5.450686e-07), ('4', 4.26429e-07), ('5', 4.80477e-07), ('6', 4.7158027e-07), ('7', 1.3078858e-07), ('8', 3.0263837e-06), ('9', -1.184744e-07), ('10', 3.4644008e-07), ('11', 2.907229e-07), ('12', 1.5489387e-07), ('13', 6.4607772e-07), ('14', 4.0343631e-07), ('15', 6.390094e-07), ('16', 5.4843275e-07), ('17', 6.0720986e-07), ('18', 7.4953972e-07), ('19', 3.3182587e-07), ('20', 4.5287439e-07), ('21', 3.6134358e-07), ('22', 5.9534886e-07), ('23', 4.4319706e-07), ('24', 6.8872364e-07), ('25', 6.2317008e-07), ('26', 4.8852969e-07), ('27', 4.9597992e-07), ('28', 1.0797711e-06), ('29', 1.7507358e-07), ('30', -2.1859263e-07), ('31', 5.0827134e-07), ('32', 5.2044582e-07), ('33', 4.8782776e-07), ('34', 6.3227527e-07), ('35', 5.2390256e-07), ('36', 4.2647226e-07), ('37', 4.2647226e-07), ('38', 4.8052841e-07), ('39', 4.1547839e-07), ('morphing_basis_

16:07 madminer.utils.inter WARNING Found 44 negative weights in event: OrderedDict([('sm', -4.80477e-07), ('1', -6.216743e-07), ('2', -3.7030937e-07), ('3', -6.216743e-07), ('4', -3.7030937e-07), ('5', -4.80477e-07), ('6', -4.1605202e-07), ('7', -6.4010579e-07), ('8', 5.0699377e-07), ('9', -8.8186944e-07), ('10', -4.3443725e-07), ('11', -5.1247249e-07), ('12', -4.636685e-08), ('13', -5.1657496e-07), ('14', -4.6972144e-07), ('15', -1.7121891e-07), ('16', -5.7841348e-07), ('17', -3.096887e-07), ('18', -5.4024693e-07), ('19', -5.6702652e-07), ('20', -5.6602638e-07), ('21', -1.9756849e-06), ('22', -5.8580497e-07), ('23', -4.5792421e-07), ('24', -5.6093188e-07), ('25', -5.7374117e-07), ('26', -4.7060134e-07), ('27', -5.1681005e-07), ('28', -5.0697374e-07), ('29', -1.8243794e-07), ('30', -3.5394124e-07), ('31', -5.5592681e-07), ('32', -4.9407817e-07), ('33', -6.0271288e-07), ('34', -5.2106281e-07), ('35', -4.7017097e-07), ('36', -3.703843e-07), ('37', -3.703843e-07), ('38', -4.8057306e-07), 

16:07 madminer.utils.inter WARNING Found 4 negative weights in event: OrderedDict([('sm', 4.80477e-07), ('1', 3.9345096e-07), ('2', 5.3164348e-07), ('3', 3.9345096e-07), ('4', 5.3164348e-07), ('5', 4.80477e-07), ('6', 4.8713556e-07), ('7', -2.5802155e-08), ('8', 4.4083867e-06), ('9', -4.299559e-07), ('10', 3.2529214e-07), ('11', 2.2634861e-07), ('12', 2.2776202e-07), ('13', 6.5719654e-07), ('14', 3.8675e-07), ('15', 8.0074828e-07), ('16', 5.3018363e-07), ('17', 7.0751626e-07), ('18', 8.0106471e-07), ('19', 2.5781237e-07), ('20', 4.1336186e-07), ('21', -2.3929535e-07), ('22', 5.8610059e-07), ('23', 4.4140486e-07), ('24', 7.1638636e-07), ('25', 6.2680889e-07), ('26', 4.9468937e-07), ('27', 4.8555965e-07), ('28', 1.2393344e-06), ('29', 2.0707225e-07), ('30', -3.6593072e-07), ('31', 4.860311e-07), ('32', 5.2684168e-07), ('33', 4.4114108e-07), ('34', 6.5945346e-07), ('35', 5.4033894e-07), ('36', 5.3161471e-07), ('37', 5.3161471e-07), ('38', 4.8042545e-07), ('39', 5.4255258e-07), ('morphing_

16:07 madminer.utils.inter WARNING Found 44 negative weights in event: OrderedDict([('sm', -4.80477e-07), ('1', -5.9034616e-07), ('2', -3.9325123e-07), ('3', -5.9034616e-07), ('4', -3.9325123e-07), ('5', -4.80477e-07), ('6', -4.1667015e-07), ('7', -6.0053243e-07), ('8', 6.5154897e-08), ('9', -8.0339381e-07), ('10', -4.3115425e-07), ('11', -4.9975866e-07), ('12', -8.2561173e-08), ('13', -5.1677842e-07), ('14', -4.6843949e-07), ('15', -2.2160689e-07), ('16', -5.6959643e-07), ('17', -3.3893543e-07), ('18', -5.4743757e-07), ('19', -5.4776652e-07), ('20', -5.5478855e-07), ('21', -1.7756909e-06), ('22', -5.7610015e-07), ('23', -4.5828691e-07), ('24', -5.6251292e-07), ('25', -5.677736e-07), ('26', -4.7272294e-07), ('27', -5.098804e-07), ('28', -5.4520003e-07), ('29', -2.1174632e-07), ('30', -3.2583221e-07), ('31', -5.4515847e-07), ('32', -4.9465854e-07), ('33', -5.8273506e-07), ('34', -5.2515866e-07), ('35', -4.7504112e-07), ('36', -3.9334038e-07), ('37', -3.9334038e-07), ('38', -4.8058871e-0

## Combine samples

In [11]:
filenames_in = [sample_dir + 'samples_{}.h5'.format(i_card) for i_card in range(n_runs_per_benchmark)]

combine_and_shuffle(filenames_in, sample_dir + 'samples.h5', k_factors=1./float(n_oversampling))

16:20 madminer.sampling    WARNING Careful: this tool assumes that all samples are generated with the same setup, including identical benchmarks (and thus morphing setup). If it is used with samples with different settings, there will be wrong results! There are no explicit cross checks in place yet.
16:20 madminer.sampling    INFO    Copying setup from /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/samples/wgamma_sys/samples_0.h5 to /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/samples/wgamma_sys/samples.h5
16:20 madminer.sampling    INFO    Loading samples from file 1 / 22 at /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/samples/wgamma_sys/samples_0.h5, multiplying weights with k factor 0.5
16:20 madminer.sampling    INFO    Loading samples from file 2 / 22 at /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/samples/wgamma_sys/samples_1.h5, multiplying weights with k factor 0.5
16:20 madminer.sampling    INFO    Load

In [12]:
tight_runs = list(range(10)) + list(range(11,21))
filenames_in = [sample_dir + 'samples_tight_{}.h5'.format(i_card) for i_card in tight_runs]

combine_and_shuffle(filenames_in, sample_dir + 'samples_tight.h5', k_factors=1./float(n_oversampling))

16:21 madminer.sampling    WARNING Careful: this tool assumes that all samples are generated with the same setup, including identical benchmarks (and thus morphing setup). If it is used with samples with different settings, there will be wrong results! There are no explicit cross checks in place yet.
16:21 madminer.sampling    INFO    Copying setup from /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/samples/wgamma_sys/samples_tight_0.h5 to /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/samples/wgamma_sys/samples_tight.h5
16:21 madminer.sampling    INFO    Loading samples from file 1 / 20 at /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/samples/wgamma_sys/samples_tight_0.h5, multiplying weights with k factor 0.5
16:21 madminer.sampling    INFO    Loading samples from file 2 / 20 at /Users/johannbrehmer/work/projects/madminer/diboson_mining/data/samples/wgamma_sys/samples_tight_1.h5, multiplying weights with k factor 0.5
16:21 madminer.